**OM NAMO NARAYANA**



In [1]:
import os
import numpy as np
from tqdm import tqdm
import random
from torch.utils.data import Dataset
import torch

In [2]:
!pip install wandb
!wandb login
# log in key : 9d5065a2de6cbad8a4869ecf568cf7277676f833

     |████████████████████████████████| 1.7 MB 5.8 MB/s 
     |████████████████████████████████| 143 kB 45.9 MB/s 
     |████████████████████████████████| 180 kB 45.0 MB/s 
     |████████████████████████████████| 63 kB 1.4 MB/s 
  Created wheel for pathtools: filename=pathtools-0.1.2-py3-none-any.whl size=8806 sha256=3dc5735cee84371b2dd489161304c4bf7bf2b0cbc09d8feee821767d81ad8c04
  Stored in directory: /root/.cache/pip/wheels/3e/31/09/fa59cef12cdcfecc627b3d24273699f390e71828921b2cbba2
Successfully built pathtools
wandb: You can find your API key in your browser here: https://wandb.ai/authorize
wandb: Paste an API key from your profile and hit enter, or press ctrl+c to quit: 
wandb: Appending key for api.wandb.ai to your netrc file: /root/.netrc


In [3]:
import wandb

wandb.init(project="finetuning-GPT-2", entity="team-knitts")

wandb: Currently logged in as: team-knitts (use `wandb login --relogin` to force relogin)


In [4]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [5]:
root_path = '/content/drive/My Drive/dataset/train/train/'
text_file_names = os.listdir(root_path)
dataset = []

for file_name in tqdm(text_file_names):
  with open(root_path + file_name, 'r') as f:
    dataset.append([f.read()])

print(dataset[:2])

100%|██████████| 357/357 [00:08<00:00, 41.07it/s] 

[['<doc id="1505" url="https://ta.wikipedia.org/wiki?curid=1505" title="ஆல்பர்ட் ஐன்ஸ்டைன்">\nஆல்பர்ட் ஐன்ஸ்டைன்\n\nஆல்பர்ட் ஐன்ஸ்டைன் ("Albert Einstein", மார்ச் 14, 1879 – ஏப்ரல் 18, 1955) குறிப்பிடத்தக்க பயன்பாட்டுக் கணிதத் திறமைகள் கொண்ட, ஒரு கோட்பாட்டு இயற்பியல் அறிஞர் ஆவார். இருபதாம் நூற்றாண்டின் மிக முக்கியமான அறிவியலாளராகப் பொதுவாகக் கருதப்படுகிறார். இவர் புகழ்பெற்ற சார்புக் கோட்பாட்டை முன்வைத்ததுடன், குவாண்டம் எந்திரவியல், புள்ளியியற் எந்திரவியல் மற்றும் அண்டவியல் ஆகிய துறைகளிலும் குறிப்பிடத்தக்க பங்களிப்புகளைச் செய்துள்ளார். ஒளி மின் விளைவைக் கண்டுபிடித்து விளக்கியமைக்காகவும், கோட்பாட்டு இயற்பியலில் அவர் செய்த சேவைக்காகவும், 1921ல் இவருக்கு இயற்பியலுக்கான நோபல் பரிசு வழங்கப்பட்டது.\n\nதற்காலத்தில் பொதுப் பயன்பாட்டில் ஐன்ஸ்டைன் என்ற சொல், அதிக புத்திக்கூர்மையுள்ள ஒருவரைக் குறிக்கும் சொல்லாக மாறிவிட்டது. 1999 ல், புதிய ஆயிரவாண்டைக் குறித்து வெளியிடப்பட்ட டைம் (இதழ்), "இந்த நூற்றாண்டின் சிறந்த மனிதர்" என்ற பெயரை ஐன்ஸ்டீனுக்கு வழங்கியது.\n\nஐன்ஸ்டைன் ஜெர்மனியில், வுர்ட்டெம்பர்க் இ

In [6]:
import re
dataset_processed = []
for tdata in tqdm(dataset):
  tdata = re.split('<?doc .*>|\n', tdata[0])[1:]
  dataset_processed.append(list(filter(None, [tdata_.strip('</doc>\n') for tdata_ in tdata])))
print(np.array(dataset_processed).shape, dataset_processed[:2])

dataset_combined = []
for data in dataset_processed:
  dataset_combined += data
del dataset_processed

100%|██████████| 357/357 [00:11<00:00, 31.98it/s]
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:6: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray
  


(357,) [['ஆல்பர்ட் ஐன்ஸ்டைன்', 'ஆல்பர்ட் ஐன்ஸ்டைன் ("Albert Einstein", மார்ச் 14, 1879 – ஏப்ரல் 18, 1955) குறிப்பிடத்தக்க பயன்பாட்டுக் கணிதத் திறமைகள் கொண்ட, ஒரு கோட்பாட்டு இயற்பியல் அறிஞர் ஆவார். இருபதாம் நூற்றாண்டின் மிக முக்கியமான அறிவியலாளராகப் பொதுவாகக் கருதப்படுகிறார். இவர் புகழ்பெற்ற சார்புக் கோட்பாட்டை முன்வைத்ததுடன், குவாண்டம் எந்திரவியல், புள்ளியியற் எந்திரவியல் மற்றும் அண்டவியல் ஆகிய துறைகளிலும் குறிப்பிடத்தக்க பங்களிப்புகளைச் செய்துள்ளார். ஒளி மின் விளைவைக் கண்டுபிடித்து விளக்கியமைக்காகவும், கோட்பாட்டு இயற்பியலில் அவர் செய்த சேவைக்காகவும், 1921ல் இவருக்கு இயற்பியலுக்கான நோபல் பரிசு வழங்கப்பட்டது.', 'தற்காலத்தில் பொதுப் பயன்பாட்டில் ஐன்ஸ்டைன் என்ற சொல், அதிக புத்திக்கூர்மையுள்ள ஒருவரைக் குறிக்கும் சொல்லாக மாறிவிட்டது. 1999 ல், புதிய ஆயிரவாண்டைக் குறித்து வெளியிடப்பட்ட டைம் (இதழ்), "இந்த நூற்றாண்டின் சிறந்த மனிதர்" என்ற பெயரை ஐன்ஸ்டீனுக்கு வழங்கியது.', 'ஐன்ஸ்டைன் ஜெர்மனியில், வுர்ட்டெம்பர்க் இலுள்ள உல்ம் என்னுமிடத்தில், 1879 ஆம் ஆண்டு பிறந்தார். இவரது தந்தையார், ஹேர்மன் ஐன்ஸ்

In [7]:
# comment for training
# dataset_combined = dataset_combined[:100] # uncomment for testing

In [8]:
dataset_combined[:2]

['ஆல்பர்ட் ஐன்ஸ்டைன்',
 'ஆல்பர்ட் ஐன்ஸ்டைன் ("Albert Einstein", மார்ச் 14, 1879 – ஏப்ரல் 18, 1955) குறிப்பிடத்தக்க பயன்பாட்டுக் கணிதத் திறமைகள் கொண்ட, ஒரு கோட்பாட்டு இயற்பியல் அறிஞர் ஆவார். இருபதாம் நூற்றாண்டின் மிக முக்கியமான அறிவியலாளராகப் பொதுவாகக் கருதப்படுகிறார். இவர் புகழ்பெற்ற சார்புக் கோட்பாட்டை முன்வைத்ததுடன், குவாண்டம் எந்திரவியல், புள்ளியியற் எந்திரவியல் மற்றும் அண்டவியல் ஆகிய துறைகளிலும் குறிப்பிடத்தக்க பங்களிப்புகளைச் செய்துள்ளார். ஒளி மின் விளைவைக் கண்டுபிடித்து விளக்கியமைக்காகவும், கோட்பாட்டு இயற்பியலில் அவர் செய்த சேவைக்காகவும், 1921ல் இவருக்கு இயற்பியலுக்கான நோபல் பரிசு வழங்கப்பட்டது.']

In [9]:
import pandas as pd

In [10]:
def corrupt_dataset(data):
  x = np.random.randint(2, size=1)[0]
  l = len(data) 
  s = int(len(data)/10)
  new_data = data
  if(x):
    label = 1
    places = [0] + list(np.random.randint(1, l-1, size=s))
    places.sort()

    ### logic to be optimized
    for i in range(len(places)-1):
      new_data += data[places[i]:places[i+1]-1]
    # new_data = data[:places[0]-1] + data[places[0] : places[1]-1] + data[places[1]:]
  else:
    places = [-1, -1]
    label = 0
  return {'data' : new_data, 'label' : label, 'places' : places }

In [11]:
corrupted_dataset = pd.DataFrame(list(map(corrupt_dataset, tqdm(dataset_combined))))
del corrupted_dataset['places']
pd_dataset = pd.DataFrame(corrupted_dataset)
del corrupt_dataset
del dataset_combined
pd_dataset.head()

100%|██████████| 571391/571391 [01:31<00:00, 6235.10it/s] 


data  label
0                                 ஆல்பர்ட் ஐன்ஸ்டைன்      0
1  ஆல்பர்ட் ஐன்ஸ்டைன் ("Albert Einstein", மார்ச் ...      0
2  தற்காலத்தில் பொதுப் பயன்பாட்டில் ஐன்ஸ்டைன் என்...      0
3  ஐன்ஸ்டைன் ஜெர்மனியில், வுர்ட்டெம்பர்க் இலுள்ள ...      0
4  இவரது தந்தையாருடைய தொழிலில் நட்டம் ஏற்பட்டதனால...      0

In [12]:
# device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
device = 'cpu'
torch.cuda.empty_cache()
print('Using device:', device)
print()

Using device: cpu



In [13]:
!pip install transformers

     |████████████████████████████████| 3.5 MB 5.2 MB/s 
     |████████████████████████████████| 6.8 MB 28.8 MB/s 
     |████████████████████████████████| 67 kB 4.9 MB/s 
     |████████████████████████████████| 895 kB 38.8 MB/s 
     |████████████████████████████████| 596 kB 50.4 MB/s 
  Attempting uninstall: pyyaml
    Found existing installation: PyYAML 3.13
    Uninstalling PyYAML-3.13:
      Successfully uninstalled PyYAML-3.13


In [14]:
from transformers import AutoTokenizer, AutoModelForCausalLM

tokenizer = AutoTokenizer.from_pretrained("abinayam/gpt-2-tamil")
tokenizer.pad_token = 295 # to be changed

Downloading:   0%|          | 0.00/876 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/1.53M [00:00<?, ?B/s]

Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [15]:
config = {
    'learning_rate' : 1e-4, # to be experimented
    'batch_size' : 2, # to be changed [crashing if high]
    'epochs' : 10,
    'betas': [0.9, 0.999]
}

wandb.config = config

In [16]:
from torch.utils.data import Dataset

class TamilDataset(Dataset):
    def __init__(self, dataset, target):
        self.dataset = dataset
        self.target = target

    def __len__(self):
        return len(self.dataset)


    def __getitem__(self, idx):
        # print(idx)
        batch = tokenizer(self.dataset[idx], truncation=True, max_length=1024, padding='max_length', return_tensors='pt')
        return {'data': batch['input_ids'].to(device), 'target': torch.tensor(np.array(self.target[idx], dtype=np.float32)).to(device)}

In [17]:
from torch.utils.data import DataLoader


temp = TamilDataset(list(pd_dataset['data']), list(pd_dataset['label']))
train_dataloader = DataLoader(temp, batch_size=config['batch_size'], shuffle=True)
batch = next(iter(train_dataloader))
# print(batch['data'].shape, batch['target'].shape)
# output = model(batch['data'])
# print(output.logits.shape)

In [18]:
from torch import nn
import torch.nn.functional as F

class CustomGPTModel(nn.Module):
    def __init__(self):
          super(CustomGPTModel, self).__init__()
          self.model = AutoModelForCausalLM.from_pretrained("abinayam/gpt-2-tamil")
          self.model.to(device)
          ### To be optimized
          self.linear1 = nn.Linear(50257, 1024)
          self.linear2 = nn.Linear(1024, 512)
          self.linear3 = nn.Linear(512, 1)
          self.sigmoid = nn.Sigmoid()

    def forward(self, batch):
          sequence_output= self.model(batch)

          logits = sequence_output.logits
          logits.to(device)

          # sequence_output has the following shape: (batch_size, sequence_length, 768)
          linear1_output = F.relu(self.linear1(sequence_output.logits[:,:,0,:].view(-1,50257))) ## extract the 1st token's embeddings

          linear2_output = F.relu(self.linear2(linear1_output))

          linear3_output = F.relu(self.linear3(linear2_output))


          sigmoid_output = self.sigmoid(linear3_output)

          return sigmoid_output

In [19]:
import torch.optim as optim



model = CustomGPTModel()
model.to(device)

optimizer = optim.Adam(model.parameters(), lr=config['learning_rate'], betas=config['betas'], eps=1e-08, weight_decay=0, amsgrad=False)

criterion = nn.BCELoss()

Downloading:   0%|          | 0.00/487M [00:00<?, ?B/s]

In [ ]:
epochs = config['epochs']


step = 0
for epoch in range(epochs):
  for t, batch in enumerate(train_dataloader):
  # batch = next(iter(train_dataloader))
    step += 1
    data = batch['data']
    targets = batch['target'] ## assuming that data loader returns a tuple of data and its targets
    
    optimizer.zero_grad()   
    outputs = model.forward(data)
    targets = targets.unsqueeze(1)
    loss = criterion(outputs, targets)
    wandb.log({"loss": loss.item()}, step=step)
    if(epoch % 2 == 0 and t == 0):
      print('epoch:%d t:%d loss:%.2f'%(epoch, t, loss.item()))
      wandb.log({'targets': targets.cpu(), 'outputs': outputs.cpu()}, step=step)

    loss.backward()
    optimizer.step()


epoch:0 t:0 loss:0.69
